In [ ]:
import numpy as np

In this lecture we're considering a very simple prediction problem. We are given an input $x \in \{0,1\}$, and we are trying to predict a label $t \in \{0, 1\}$. For this problem, we assume that the data generating distribution $p_{data}$ was any distribution such that $p_{data}(x) > 0$ for all $x \in \{0,1\}$. Let's consider a special case of $p_{data}$, which is given by the following table.

 &nbsp; | `x = 0` | `x = 1`
--- | --- | ---
**`t = 0`** | 9/20 | 2/20
**`t = 1`** | 6/20 | 3/20

We assume that our data is random pairs $(x, t) \sim p_{data}(x,t)$.

In [ ]:
pdata = np.array([[9/20, 2/20],
                  [6/20, 3/20]])

for (t,x) in [(0,0), (0,1), (1,0), (1,1)]:
    print(f"pdata(T={t}, X={x}) = {pdata[t,x]}")

Based on this joint distribution, we can compute the relevant marginal $p_{data}(x)$ and conditional $p_{data}(t | x)$.

In [ ]:
pdata_x = np.sum(pdata, axis=0) # sum over the axis representing T
print(repr(pdata_x))

# to get the conditional probabilities of the labels,
# divide each row by pdata_x
pdata_0givenx = pdata[0,:]/pdata_x
pdata_1givenx = pdata[1,:]/pdata_x
pdata_tgivenx = np.vstack([pdata_0givenx, pdata_1givenx])

print(repr(pdata_tgivenx))

Let us consider predictors, which are functions $y : \{0, 1\} \to \{0, 1\}$. It is not too hard to convince yourself that there are only 4 possible predictors *in the special case that we are considering*:

 &nbsp; &nbsp; &nbsp; &nbsp;| $y_i(0)$ &nbsp; &nbsp; &nbsp; &nbsp; &nbsp;  &nbsp; |$y_i(1)$   &nbsp; &nbsp; &nbsp;  &nbsp; &nbsp; &nbsp; 
--- | --- | ---
$y_0$ | 0 | 1
$y_1$ | 1 | 0
$y_2$ | 0 | 0
$y_3$ | 1 | 1


In [ ]:
def y_0(x):
  return x

def y_1(x):
  return 1 - x

def y_2(x):
  return 0

def y_3(x):
  return 1

all_predictors = [y_0, y_1, y_2, y_3]

for i, y in enumerate(all_predictors):
    print(f"y_{i+1}: y_{i}(0)={y(0)} y_{i}(1)={y(1)}")

We will score predictors based on the 0-1 loss:

$$L(y, t) = \begin{cases} 0 & \text{if } y = t\\1 &\text{if } y \neq t\end{cases}$$

Given a predictor $y$, we can compute the expected loss on the data generating distribuition:

$$\mathcal{R}[y] = \mathbb{E}_{(X,T) \sim p_{data}}[L(y(X), T)] = \sum_{t \in \{0,1\}} \sum_{x \in \{0,1\}} p_{data}(x,t) L(y(x), t)$$

Given a predictor $y$ and a data set $\mathcal{D}$ with $N$ data points, we can compute the average loss:

$$\hat{\mathcal{R}}[y, \mathcal{D}] = \sum_{(x^{(i)}, t^{(i)}) \in \mathcal{D}} \frac{1}{N} L(y(x^{(i)}), t^{(i)})$$


In [ ]:
def loss(prediction, t):
  """The 0-1 loss function."""
  return int(prediction != t)

def expected_loss(y, pdata):
  """Compute the expected loss of y : {0,1} -> {0,1}."""
  L = 0
  for t in [0, 1]:
    for x in [0, 1]:
      L = L + pdata[t, x] * loss(y(x), t)
  return L

def average_loss(y, D):
  """Compute the average loss of y : {0,1} -> {0,1}."""
  N = len(D)
  L = 0
  for (xi, ti) in D:
    L = L + loss(y(xi), ti) 
  return L / N

Let's evaluate the predictors $y_i$ on expected loss $\mathcal{R}[y_i]$ under the data generating distribution. Which predictor is optimal?

In [ ]:
predictor_losses = [expected_loss(y, pdata) for y in all_predictors]
for i, predictor_loss in enumerate(predictor_losses):
  print(f"R[y_{i}]=" + "{:.2f}".format(predictor_loss))

optimal_predictor = np.argmin(predictor_losses)
# Report
print(f"Optimal predictor y*: y_{optimal_predictor}")

We've just computed

$$y^* = \arg \min_{y: \{0,1\} \to \{0,1\}} \mathcal{R}[y]$$

Let's now see how we can *learn* this predictor from a finite training set. First, let's write a function for generating data sets.


In [ ]:
def sample_data_set(N, pdata):
  """Sample a data set according to the data generating distribution"""
  D = []
  for i in range(N):
    # First, sample x.
    # The reason we can do this, is because of the rules of probability.
    # p(t,x) = p(x)p(t | x)

    # pdata_x = [p(X=0), p(X=1)]
    pdata_x = np.sum(pdata, axis=0) # sum over the axis representing T
    x = np.random.choice([0, 1], p=pdata_x)

    
    # Now we sample t given x.
    # pdata_tgivenx = [p(T=0 | X=x), p(T=1 | X=x)]
    pdata_0givenx = pdata[0,:]/pdata_x
    pdata_1givenx = pdata[1,:]/pdata_x
    pdata_tgivenx = np.vstack([pdata_0givenx, pdata_1givenx])
    conditional_in_this_realization = pdata_tgivenx[:,x]
    t = np.random.choice([0,1], p=conditional_in_this_realization)

    # Add (x,t) to training set
    D.append((x, t))
  return D

Let's sample a finite training set $\mathcal{D}^{train}$. 

In [ ]:
N = 3
train_set = sample_data_set(N, pdata)
print("Training set")
for i, (x, t) in enumerate(train_set):
  print(f"x_{i}: {x}  t_{i}: {t}")

Our high level goal is to calculate

$$\hat{y}^* = \arg \min_{y : \{0,1\} \to \{0,1\}} \hat{\mathcal{R}}[y, \mathcal{D}^{train}]$$

In our case, we can do this explicitly by evaluating all of the predictors in terms of average loss $\hat{\mathcal{R}}[y_i, \mathcal{D}^{train}]$ on the training set and picking the best one $\hat{y}^{\star}$. Which one did we pick?

In [ ]:
N = 5
train_set = sample_data_set(N, pdata)

predictor_losses = [average_loss(y, train_set) for y in all_predictors]
# for i, predictor_loss in enumerate(predictor_losses):
#   print(f"y_{i+1} average training loss: " + "{:.2f}".format(predictor_loss))

# This code finds the predictor with the minimum training loss
which_predictor = np.argmin(predictor_losses)
best_predictor = all_predictors[which_predictor]

# Report
print(f"\nBest predictor on train set hat(y)^*: y_{which_predictor}")
print("Expected loss of best train predictor: {:.2f}".format(expected_loss(best_predictor, pdata)))

If you run the previous cell a few times, you'll see that the best predictor $\hat{y}^{\star}$ is *random*, because our training set was *random*. Let's automate this process and see *how often* we pick the optimal predictor $\hat{y}^{\star} = y^*$ from random training sets.

In [ ]:
def pick_predictor(train_set, hypothesis_space):
  """Pick the best predictor on this train set."""
  predictor_losses = [average_loss(y, train_set) for y in hypothesis_space]
  i = np.argmin(predictor_losses)
  return hypothesis_space[i], i

With the code below you can vary the size of training sets $N$ and the number of random training runs to estimate the probability of picking the optimal predictor. Notice, as $N \to \infty$, we end up always picking $y^*$. What happens as $N \to \infty$? Try `N = 1`, `N = 100`, `N = 500`, to see if there's a trend.

In [ ]:
N = 500
runs = 100

how_often_optimal = 0
for j in range(runs):
  # Sampling a new training set of size N
  train_set = sample_data_set(N, pdata)

  # Pick the best predictor
  predictor, which_predictor = pick_predictor(train_set, all_predictors)
  how_often_optimal += (which_predictor == 0)
    

# Report
print((f"\nTraining set size: {N}"+
       f"\nOptimal predictor y_0 picked: {how_often_optimal/runs * 100}% of {runs} training runs"))

Finally, let's investigate evaluating predictors using a test set. The following code computes an average test loss to approximate the expected loss, $\hat{\mathcal{R}}[\hat{y}^{\star}, \mathcal{D}^{test}] \approx \mathcal{R}[\hat{y}^{\star}]$. 

Try a few values of `train_N`. How do the average train loss, average test loss, and expected loss compare?

In [ ]:
train_N = 1000
test_N = 1000
test_set = sample_data_set(test_N, pdata)
train_set = sample_data_set(train_N, pdata)

# Pick the best predictor
predictor, which_predictor = pick_predictor(train_set, all_predictors)

# Report
print((f"Best predictor on train: y_{which_predictor} "+
       f"\nExpected loss of best train predictor: {expected_loss(predictor, pdata):.2f}" +
       f"\nAverage test loss of best train predictor: {average_loss(predictor, test_set):.2f} on test set of size {test_N}" +
       f"\nAverage train loss of best train predictor: {average_loss(predictor, train_set):.2f} on train set of size {train_N}."
      ))

You should have noticed in the previous cell that the train loss is often an under-estimate of the expected loss, especially when the train set is small. This is an illustration of the problem with using train losses to forecast your loss on unseen data.

It turns out that we can write down an explicit formula for the optimal predictor. This formula depends on the data generating distribution in a specific way. The optimal predictor is given by:

$$y^*(x) = \arg\max_{t \in \{0,1\}} p_{data}(t | x)$$

Can you *prove* that this is always the optimal predictor for a fixed $p_{data}$?